In [ ]:
import numpy as np
import pandas as pd
import json
import random
import tensorflow as tf
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Model, load_model
from tensorflow.keras.layers import (
    Input,
    LSTM,
    Dense,
    Embedding,
    Bidirectional,
    Concatenate,
    Attention,
    Dropout,
)
from tensorflow.keras.callbacks import ModelCheckpoint, EarlyStopping
from sklearn.model_selection import train_test_split
import matplotlib.pyplot as plt
import re

In [8]:
with open("data_converted.json", "r") as f:
    data = json.load(f)
    
# Preprocessing function
def preprocess_text(text):
    """Melakukan preprocessing teks dasar"""
    text = text.lower()
    text = re.sub(r"\s+", " ", text).strip()
    return text


# Persiapkan data untuk model
def prepare_data(data):
    """Siapkan data untuk model"""
    contexts = []
    tokens_list = []
    ner_list = []
    srl_list = []
    questions = []
    answers = []
    q_types = []

    for item in data:
        for qa in item["qas"]:
            contexts.append(preprocess_text(item["context"]))
            tokens_list.append(item["tokens"])
            ner_list.append(item["ner"])
            srl_list.append(item["srl"])
            questions.append(preprocess_text(qa["question"]))
            answers.append(qa["answer"])
            q_types.append(qa["type"])

    return contexts, tokens_list, ner_list, srl_list, questions, answers, q_types


contexts, tokens_list, ner_list, srl_list, questions, answers, q_types = prepare_data(
    data
)

In [9]:
max_vocab_size = 10000
tokenizer = Tokenizer(num_words=max_vocab_size, oov_token="<OOV>")
tokenizer.fit_on_texts(contexts + questions + [" ".join(item) for item in tokens_list])
vocab_size = len(tokenizer.word_index) + 1

# Encoding untuk NER
ner_tokenizer = Tokenizer(oov_token="<OOV>")
ner_tokenizer.fit_on_texts([" ".join(ner) for ner in ner_list])
ner_vocab_size = len(ner_tokenizer.word_index) + 1

# Encoding untuk SRL
srl_tokenizer = Tokenizer(oov_token="<OOV>")
srl_tokenizer.fit_on_texts([" ".join(srl) for srl in srl_list])
srl_vocab_size = len(srl_tokenizer.word_index) + 1

# Encoding untuk tipe pertanyaan
q_type_tokenizer = Tokenizer()
q_type_tokenizer.fit_on_texts(q_types)
q_type_vocab_size = len(q_type_tokenizer.word_index) + 1


# Konversi token, ner, srl ke sequences
def tokens_to_sequences(tokens, ner, srl):
    """Konversi token, ner, dan srl ke sequences"""
    token_seqs = [tokenizer.texts_to_sequences([" ".join(t)])[0] for t in tokens]
    ner_seqs = [ner_tokenizer.texts_to_sequences([" ".join(n)])[0] for n in ner]
    srl_seqs = [srl_tokenizer.texts_to_sequences([" ".join(s)])[0] for s in srl]
    return token_seqs, ner_seqs, srl_seqs


# Menentukan panjang maksimum untuk padding
context_seqs = tokenizer.texts_to_sequences(contexts)
question_seqs = tokenizer.texts_to_sequences(questions)
token_seqs, ner_seqs, srl_seqs = tokens_to_sequences(tokens_list, ner_list, srl_list)

max_context_len = max([len(seq) for seq in context_seqs])
max_question_len = max([len(seq) for seq in question_seqs])
max_token_len = max([len(seq) for seq in token_seqs])


# Pad sequences untuk memastikan semua input sama panjang
def pad_all_sequences(context_seqs, question_seqs, token_seqs, ner_seqs, srl_seqs):
    """Padding semua sequences"""
    context_padded = pad_sequences(context_seqs, maxlen=max_context_len, padding="post")
    question_padded = pad_sequences(
        question_seqs, maxlen=max_question_len, padding="post"
    )
    token_padded = pad_sequences(token_seqs, maxlen=max_token_len, padding="post")
    ner_padded = pad_sequences(ner_seqs, maxlen=max_token_len, padding="post")
    srl_padded = pad_sequences(srl_seqs, maxlen=max_token_len, padding="post")
    return context_padded, question_padded, token_padded, ner_padded, srl_padded


# Siapkan encoder untuk jawaban
answer_tokenizer = Tokenizer(oov_token="<OOV>")
answer_tokenizer.fit_on_texts(answers)
answer_vocab_size = len(answer_tokenizer.word_index) + 1

# Encode tipe pertanyaan - FIX - Menggunakan indeks langsung bukan sequence
q_type_indices = []
for q_type in q_types:
    # Dapatkan indeks tipe pertanyaan (dikurangi 1 karena indeks dimulai dari 1)
    q_type_idx = q_type_tokenizer.word_index.get(q_type, 0)
    q_type_indices.append(q_type_idx)

# Konversi ke numpy array
q_type_indices = np.array(q_type_indices)

# One-hot encode tipe pertanyaan
q_type_categorical = tf.keras.utils.to_categorical(
    q_type_indices, num_classes=q_type_vocab_size
)

# Pad sequences
context_padded, question_padded, token_padded, ner_padded, srl_padded = (
    pad_all_sequences(context_seqs, question_seqs, token_seqs, ner_seqs, srl_seqs)
)

# Encode jawaban
answer_seqs = answer_tokenizer.texts_to_sequences(answers)
max_answer_len = max([len(seq) for seq in answer_seqs])
answer_padded = pad_sequences(answer_seqs, maxlen=max_answer_len, padding="post")

# Split data menjadi train dan test sets
indices = list(range(len(context_padded)))
train_indices, test_indices = train_test_split(indices, test_size=0.2, random_state=42)



In [10]:

# Fungsi untuk mendapatkan subset dari data berdasarkan indices
def get_subset(data, indices):
    return np.array([data[i] for i in indices])


# Train data
train_context = get_subset(context_padded, train_indices)
train_question = get_subset(question_padded, train_indices)
train_token = get_subset(token_padded, train_indices)
train_ner = get_subset(ner_padded, train_indices)
train_srl = get_subset(srl_padded, train_indices)
train_q_type = get_subset(q_type_categorical, train_indices)
train_answer = get_subset(answer_padded, train_indices)

# Test data
test_context = get_subset(context_padded, test_indices)
test_question = get_subset(question_padded, test_indices)
test_token = get_subset(token_padded, test_indices)
test_ner = get_subset(ner_padded, test_indices)
test_srl = get_subset(srl_padded, test_indices)
test_q_type = get_subset(q_type_categorical, test_indices)
test_answer = get_subset(answer_padded, test_indices)

# Hyperparameters
embedding_dim = 100
lstm_units = 128
ner_embedding_dim = 50
srl_embedding_dim = 50
dropout_rate = 0.3

In [11]:

# Function untuk membuat model
def create_qa_model():
    # Input layers
    context_input = Input(shape=(max_context_len,), name="context_input")
    question_input = Input(shape=(max_question_len,), name="question_input")
    token_input = Input(shape=(max_token_len,), name="token_input")
    ner_input = Input(shape=(max_token_len,), name="ner_input")
    srl_input = Input(shape=(max_token_len,), name="srl_input")
    q_type_input = Input(shape=(q_type_vocab_size,), name="q_type_input")

    # Shared embedding layer for text
    text_embedding = Embedding(vocab_size, embedding_dim, name="text_embedding")

    # Embedding untuk NER dan SRL
    ner_embedding = Embedding(ner_vocab_size, ner_embedding_dim, name="ner_embedding")(
        ner_input
    )
    srl_embedding = Embedding(srl_vocab_size, srl_embedding_dim, name="srl_embedding")(
        srl_input
    )

    # Apply embeddings
    context_embed = text_embedding(context_input)
    question_embed = text_embedding(question_input)
    token_embed = text_embedding(token_input)

    # Bi-directional LSTM untuk context dan token-level features
    context_lstm = Bidirectional(
        LSTM(lstm_units, return_sequences=True, name="context_lstm")
    )(context_embed)
    question_lstm = Bidirectional(
        LSTM(lstm_units, return_sequences=True, name="question_lstm")
    )(question_embed)

    # Concat token features (tokens, NER, SRL)
    token_features = Concatenate(name="token_features")(
        [token_embed, ner_embedding, srl_embedding]
    )
    token_lstm = Bidirectional(
        LSTM(lstm_units, return_sequences=True, name="token_lstm")
    )(token_features)

    # Attention mechanism untuk context dengan memperhatikan question
    context_attention = tf.keras.layers.Attention(name="context_attention")(
        [context_lstm, question_lstm]
    )

    # Pool attention outputs
    context_att_pool = tf.keras.layers.GlobalMaxPooling1D(name="context_att_pool")(
        context_attention
    )
    question_pool = tf.keras.layers.GlobalMaxPooling1D(name="question_pool")(
        question_lstm
    )
    token_pool = tf.keras.layers.GlobalMaxPooling1D(name="token_pool")(token_lstm)

    # Concat all features
    all_features = Concatenate(name="all_features")(
        [context_att_pool, question_pool, token_pool, q_type_input]
    )

    # Dense layers
    x = Dense(256, activation="relu", name="dense_1")(all_features)
    x = Dropout(dropout_rate)(x)
    x = Dense(128, activation="relu", name="dense_2")(x)
    x = Dropout(dropout_rate)(x)

    # Output layer untuk jawaban
    answer_output = Dense(
        answer_vocab_size, activation="softmax", name="answer_output"
    )(x)

    # Create model
    model = Model(
        inputs=[
            context_input,
            question_input,
            token_input,
            ner_input,
            srl_input,
            q_type_input,
        ],
        outputs=answer_output,
    )

    # Compile model
    model.compile(
        optimizer="adam", loss="sparse_categorical_crossentropy", metrics=["accuracy"]
    )

    return model


# Buat model
model = create_qa_model()
model.summary()


Model: "functional_1"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ context_input       │ (None, 31)        │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ question_input      │ (None, 12)        │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ token_input         │ (None, 31)        │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ ner_input           │ (None, 31)        │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ srl_input           │ (None, 31)        │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ text_embedding      │ (None, 31, 100)   │    146,000 │ context_input[0]… │
│ (Embedding)         │                   │            │ question_input[0… │
│                     │                   │            │ token_input[0][0] │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ ner_embedding       │ (None, 31, 50)    │      1,550 │ ner_input[0][0]   │
│ (Embedding)         │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ srl_embedding       │ (None, 31, 50)    │      1,150 │ srl_input[0][0]   │
│ (Embedding)         │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ bidirectional_3     │ (None, 31, 256)   │    234,496 │ text_embedding[0… │
│ (Bidirectional)     │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ bidirectional_4     │ (None, 12, 256)   │    234,496 │ text_embedding[1… │
│ (Bidirectional)     │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ token_features      │ (None, 31, 200)   │          0 │ text_embedding[2… │
│ (Concatenate)       │                   │            │ ner_embedding[0]… │
│                     │                   │            │ srl_embedding[0]… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ context_attention   │ (None, 31, 256)   │          0 │ bidirectional_3[… │
│ (Attention)         │                   │            │ bidirectional_4[… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ bidirectional_5     │ (None, 31, 256)   │    336,896 │ token_features[0… │
│ (Bidirectional)     │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ context_att_pool    │ (None, 256)       │          0 │ context_attentio… │
│ (GlobalMaxPooling1… │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ question_pool       │ (None, 256)       │          0 │ bidirectional_4[… │
│ (GlobalMaxPooling1… │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ token_pool          │ (None, 256)       │          0 │ bidirectional_5[… │
│ (GlobalMaxPooling1… │                   │            │                 

 Total params: 1,282,120 (4.89 MB)

 Trainable params: 1,282,120 (4.89 MB)

 Non-trainable params: 0 (0.00 B)

In [12]:

# Callback untuk menyimpan model terbaik
checkpoint = ModelCheckpoint(
    "qa_lstm_model.h5", monitor="val_accuracy", save_best_only=True, verbose=1
)

early_stop = EarlyStopping(monitor="val_accuracy", patience=5, verbose=1)

# Training
batch_size = 8
epochs = 50

# Ubah format jawaban untuk sparse categorical crossentropy
train_answer_labels = train_answer[:, 0]  # Ambil indeks pertama dari jawaban
test_answer_labels = test_answer[:, 0]

# Train model
history = model.fit(
    [train_context, train_question, train_token, train_ner, train_srl, train_q_type],
    train_answer_labels,
    batch_size=batch_size,
    epochs=epochs,
    validation_data=(
        [test_context, test_question, test_token, test_ner, test_srl, test_q_type],
        test_answer_labels,
    ),
    callbacks=[checkpoint, early_stop],
)

model.save("qa_lstm_model_final.keras")

# Simpan tokenizer
tokenizer_data = {
    "word_tokenizer": tokenizer.to_json(),
    "ner_tokenizer": ner_tokenizer.to_json(),
    "srl_tokenizer": srl_tokenizer.to_json(),
    "answer_tokenizer": answer_tokenizer.to_json(),
    "q_type_tokenizer": q_type_tokenizer.to_json(),
    "max_context_len": max_context_len,
    "max_question_len": max_question_len,
    "max_token_len": max_token_len,
}

with open("qa_tokenizers.json", "w") as f:
    json.dump(tokenizer_data, f)


Epoch 1/50
140/143 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step - accuracy: 0.0361 - loss: 6.2416
Epoch 1: val_accuracy improved from -inf to 0.09825, saving model to qa_lstm_model.h5


143/143 ━━━━━━━━━━━━━━━━━━━━ 6s 21ms/step - accuracy: 0.0364 - loss: 6.2299 - val_accuracy: 0.0982 - val_loss: 5.1985
Epoch 2/50
142/143 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - accuracy: 0.0967 - loss: 4.9762
Epoch 2: val_accuracy improved from 0.09825 to 0.11579, saving model to qa_lstm_model.h5


143/143 ━━━━━━━━━━━━━━━━━━━━ 2s 17ms/step - accuracy: 0.0966 - loss: 4.9756 - val_accuracy: 0.1158 - val_loss: 4.8629
Epoch 3/50
142/143 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - accuracy: 0.1214 - loss: 4.6133
Epoch 3: val_accuracy improved from 0.11579 to 0.19649, saving model to qa_lstm_model.h5


143/143 ━━━━━━━━━━━━━━━━━━━━ 2s 17ms/step - accuracy: 0.1213 - loss: 4.6122 - val_accuracy: 0.1965 - val_loss: 4.6600
Epoch 4/50
141/143 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - accuracy: 0.1587 - loss: 4.2478
Epoch 4: val_accuracy did not improve from 0.19649
143/143 ━━━━━━━━━━━━━━━━━━━━ 2s 16ms/step - accuracy: 0.1591 - loss: 4.2473 - val_accuracy: 0.1860 - val_loss: 4.4859
Epoch 5/50
141/143 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - accuracy: 0.1761 - loss: 4.1033
Epoch 5: val_accuracy improved from 0.19649 to 0.20702, saving model to qa_lstm_model.h5


143/143 ━━━━━━━━━━━━━━━━━━━━ 2s 17ms/step - accuracy: 0.1763 - loss: 4.1032 - val_accuracy: 0.2070 - val_loss: 4.5443
Epoch 6/50
140/143 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - accuracy: 0.2003 - loss: 3.8885
Epoch 6: val_accuracy improved from 0.20702 to 0.21053, saving model to qa_lstm_model.h5


...

143/143 ━━━━━━━━━━━━━━━━━━━━ 3s 18ms/step - accuracy: 0.5633 - loss: 1.5138 - val_accuracy: 0.4035 - val_loss: 4.9617
Epoch 21/50
141/143 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step - accuracy: 0.6151 - loss: 1.3638
Epoch 21: val_accuracy did not improve from 0.40351
143/143 ━━━━━━━━━━━━━━━━━━━━ 2s 17ms/step - accuracy: 0.6148 - loss: 1.3654 - val_accuracy: 0.3895 - val_loss: 5.1762
Epoch 22/50
143/143 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step - accuracy: 0.6309 - loss: 1.3643
Epoch 22: val_accuracy improved from 0.40351 to 0.41754, saving model to qa_lstm_model.h5


143/143 ━━━━━━━━━━━━━━━━━━━━ 3s 24ms/step - accuracy: 0.6309 - loss: 1.3640 - val_accuracy: 0.4175 - val_loss: 5.5482
Epoch 23/50
142/143 ━━━━━━━━━━━━━━━━━━━━ 0s 23ms/step - accuracy: 0.6541 - loss: 1.2232
Epoch 23: val_accuracy improved from 0.41754 to 0.42456, saving model to qa_lstm_model.h5


143/143 ━━━━━━━━━━━━━━━━━━━━ 4s 26ms/step - accuracy: 0.6539 - loss: 1.2237 - val_accuracy: 0.4246 - val_loss: 5.4584
Epoch 24/50
143/143 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step - accuracy: 0.6621 - loss: 1.0867
Epoch 24: val_accuracy improved from 0.42456 to 0.43509, saving model to qa_lstm_model.h5


143/143 ━━━━━━━━━━━━━━━━━━━━ 4s 28ms/step - accuracy: 0.6621 - loss: 1.0872 - val_accuracy: 0.4351 - val_loss: 5.5594
Epoch 25/50
141/143 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step - accuracy: 0.6814 - loss: 1.0853
Epoch 25: val_accuracy improved from 0.43509 to 0.48070, saving model to qa_lstm_model.h5


143/143 ━━━━━━━━━━━━━━━━━━━━ 4s 28ms/step - accuracy: 0.6811 - loss: 1.0865 - val_accuracy: 0.4807 - val_loss: 5.6930
Epoch 26/50
142/143 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step - accuracy: 0.6909 - loss: 0.9925
Epoch 26: val_accuracy did not improve from 0.48070
143/143 ━━━━━━━━━━━━━━━━━━━━ 4s 27ms/step - accuracy: 0.6908 - loss: 0.9931 - val_accuracy: 0.4175 - val_loss: 6.2907
Epoch 27/50
143/143 ━━━━━━━━━━━━━━━━━━━━ 0s 24ms/step - accuracy: 0.7164 - loss: 0.9724
Epoch 27: val_accuracy did not improve from 0.48070
143/143 ━━━━━━━━━━━━━━━━━━━━ 4s 26ms/step - accuracy: 0.7162 - loss: 0.9727 - val_accuracy: 0.4526 - val_loss: 5.9290
Epoch 28/50
143/143 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step - accuracy: 0.7475 - loss: 0.8654
Epoch 28: val_accuracy did not improve from 0.48070
143/143 ━━━━━━━━━━━━━━━━━━━━ 4s 27ms/step - accuracy: 0.7473 - loss: 0.8657 - val_accuracy: 0.4456 - val_loss: 6.3236
Epoch 29/50
143/143 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step - accuracy: 0.7654 - loss: 0.7537
Epoch 29: val_accura

In [14]:
model = load_model("qa_lstm_model_final.keras")
results = model.evaluate(
    [test_context, test_question, test_token, test_ner, test_srl, test_q_type],
    test_answer_labels,
    batch_size=batch_size,
)

print("Test Loss:", results[0])
print("Test Accuracy:", results[1])


/mnt/disc1/code/thesis_quiz_project/lstm-quiz/myenv/lib64/python3.10/site-packages/keras/src/saving/saving_lib.py:757: UserWarning: Skipping variable loading for optimizer 'rmsprop', because it has 29 variables whereas the saved optimizer has 56 variables. 
  saveable.load_own_variables(weights_store.get(inner_path))


36/36 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - accuracy: 0.4400 - loss: 7.0895
Test Loss: 6.898097991943359
Test Accuracy: 0.45614033937454224


In [ ]:
def predict_answer(context, question, tokens, ner, srl, q_type):
    # Preprocess
    context_seq = tokenizer.texts_to_sequences([preprocess_text(context)])
    question_seq = tokenizer.texts_to_sequences([preprocess_text(question)])

    # Convert token, ner, srl dengan benar (memperhatikan format yang sama dengan data training)
    token_seq = [tokenizer.texts_to_sequences([" ".join(tokens)])[0]]
    ner_seq = [ner_tokenizer.texts_to_sequences([" ".join(ner)])[0]]
    srl_seq = [srl_tokenizer.texts_to_sequences([" ".join(srl)])[0]]

    # Handle tipe pertanyaan
    q_type_idx = q_type_tokenizer.word_index.get(q_type, 0)
    q_type_cat = tf.keras.utils.to_categorical(
        [q_type_idx], num_classes=q_type_vocab_size
    )

    # Pad sequences
    context_pad = pad_sequences(context_seq, maxlen=max_context_len, padding="post")
    question_pad = pad_sequences(question_seq, maxlen=max_question_len, padding="post")
    token_pad = pad_sequences(token_seq, maxlen=max_token_len, padding="post")
    ner_pad = pad_sequences(ner_seq, maxlen=max_token_len, padding="post")
    srl_pad = pad_sequences(srl_seq, maxlen=max_token_len, padding="post")

    # Predict
    prediction = model.predict(
        [context_pad, question_pad, token_pad, ner_pad, srl_pad, q_type_cat]
    )

    # Get answer index
    answer_idx = np.argmax(prediction[0])

    # Convert to answer text
    for word, idx in answer_tokenizer.word_index.items():
        if idx == answer_idx:
            return word

    return "Unknown"
